#  Consignes

## Description

Ouvrir le fichier ks-projects-201801.csv, il recense environ 100 000 projets KickStarter. Intégrer les données directement avec L'API Python dans une base de données Mongo. 

Il conviendra de bien spécifier manuellement l'ID du document. Pensez aussi à bien formatter le type des données pour profiter des méthodes implémentées par Mongo. L'ensemble de données n'est pas forcément nécessaire, c'est à vous de créer votre modèle de données.

## Questions

- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.
- 2) Compter le nombre de projets ayant atteint leur but.
- 3) Compter le nombre de projets pour chaque catégorie.
- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.
- 6) Compter le nombre de projet ayant "Sport" dans leur nom

In [1]:
import pandas as pd
import pymongo

In [2]:
client = pymongo.MongoClient()
database = client['exercices']
collection = database['kickstarter']

In [3]:
df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")
df_ks.head()

/tmp/ipykernel_8424/2083226100.py:1: DtypeWarning: Columns (6,8,10,12) have mixed types. Specify dtype option on import or set low_memory=False.
  df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")


ID                                               name  \
0   872782264    Scott Cooper's Solo CD "A Leg Trick" (Canceled)   
1  1326492673                                    Ohceola jewelry   
2  1688410639  Sluff Off & Harald: Two latest EGGs are Classi...   
3   156812982  SketchPlanner: Create and Plan- all in one bea...   
4  1835968190    Proven sales with custom motorcycle accessories   

         category main_category currency    deadline     goal  \
0            Rock         Music      USD  2011-09-16   2000.0   
1         Fashion       Fashion      USD  2012-08-22  18000.0   
2  Tabletop Games         Games      USD  2016-07-19   2000.0   
3       Art Books    Publishing      USD  2017-09-27  13000.0   
4       Sculpture           Art      CAD  2016-02-24   5000.0   

              launched  pledged       state backers country usd pledged  \
0  2011-08-17 06:31:31   1145.0    canceled      24      US      1145.0   
1  2012-07-23 20:46:48   1851.0      failed      28      US      1851.0   
2  2016-07-01 21:55:54   7534.0  successful     254      US      3796.0   
3  2017-08-28 15:47:02  16298.0  successful     367      US      2670.0   
4  2016-01-25 17:37:10      1.0      failed       1      CA    0.708148   

   usd_pledged_real  
0       1145.000000  
1       1851.000000  
2       7534.000000  
3      16298.000000  
4          0.738225

Ce warning intervient lorsque pandas n'arrive pas à inférer le type de données. Il est sympa il précise les colones 6,8,10,12. 

In [4]:
df_ks.columns[[6,8,10,12]]

Index(['goal', 'pledged', 'backers', 'usd pledged'], dtype='object')

## Question 0

### Netoyer les données

In [26]:
df_ks['launched'] = pd.to_datetime(df_ks['launched'], format="%Y-%m-%d %H:%M:%S", errors='coerce')
df_ks['launched'].fillna(pd.Timestamp('2023-01-01'), inplace=True)
df_ks['launched_year'] = df_ks['launched'].dt.year
data = df_ks.to_dict(orient='records')
df_ks

ID                                               name  \
0        872782264    Scott Cooper's Solo CD "A Leg Trick" (Canceled)   
1       1326492673                                    Ohceola jewelry   
2       1688410639  Sluff Off & Harald: Two latest EGGs are Classi...   
3        156812982  SketchPlanner: Create and Plan- all in one bea...   
4       1835968190    Proven sales with custom motorcycle accessories   
...            ...                                                ...   
149995   574841011  Scutes Headphones - A new way to listen to you...   
149996   235190237                               My Drunk @$$ Reviews   
149997   758540498          Freedom Planet - High Speed Platform Game   
149998  1624952469                                      Clown vs Mime   
149999   891117261                            Striker's Cafe & Bakery   

              category main_category currency    deadline     goal  \
0                 Rock         Music      USD  2011-09-16   2000.0   
1              Fashion       Fashion      USD  2012-08-22  18000.0   
2       Tabletop Games         Games      USD  2016-07-19   2000.0   
3            Art Books    Publishing      USD  2017-09-27  13000.0   
4            Sculpture           Art      CAD  2016-02-24   5000.0   
...                ...           ...      ...         ...      ...   
149995  Product Design        Design      USD  2014-11-14  40000.0   
149996       Webseries  Film & Video      USD  2012-05-18   1000.0   
149997     Video Games         Games      USD  2013-02-15   2000.0   
149998       Webseries  Film & Video      USD  2011-05-27   1000.0   
149999     Food Trucks          Food      USD  2016-05-02  20000.0   

                  launched   pledged       state backers country usd pledged  \
0      2011-08-17 06:31:31    1145.0    canceled      24      US      1145.0   
1      2012-07-23 20:46:48    1851.0      failed      28      US      1851.0   
2      2016-07-01 21:55:54    7534.0  successful     254      US      3796.0   
3      2017-08-28 15:47:02   16298.0  successful     367      US      2670.0   
4      2016-01-25 17:37:10       1.0      failed       1      CA    0.708148   
...                    ...       ...         ...     ...     ...         ...   
149995 2014-10-14 20:44:37    3664.0    canceled      43      US      3664.0   
149996 2012-04-18 04:42:47       0.0      failed       0      US         0.0   
149997 2013-01-16 00:53:32  25472.69  successful    1105      US    25472.69   
149998 2011-04-27 01:22:52      76.0      failed       3      US        76.0   
149999 2016-04-03 08:01:57      29.0      failed       3      US        29.0   

        usd_pledged_real  launched_year  
0            1145.000000           2011  
1            1851.000000           2012  
2            7534.000000           2016  
3           16298.000000           2017  
4               0.738225           2016  
...                  ...            ...  
149995       3664.000000           2014  
149996          0.000000           2012  
149997      25472.690000           2013  
149998         76.000000           2011  
149999         29.000000           2016  

[150000 rows x 15 columns]

### Importer les données

In [27]:
db_kick = client.kick
kick = db_kick['test'] 
kick.insert_many(data)

InsertManyResult([ObjectId('6574895ea0c4a46f9bfb75e5'), ObjectId('6574895ea0c4a46f9bfb75e6'), ObjectId('6574895ea0c4a46f9bfb75e7'), ObjectId('6574895ea0c4a46f9bfb75e8'), ObjectId('6574895ea0c4a46f9bfb75e9'), ObjectId('6574895ea0c4a46f9bfb75ea'), ObjectId('6574895ea0c4a46f9bfb75eb'), ObjectId('6574895ea0c4a46f9bfb75ec'), ObjectId('6574895ea0c4a46f9bfb75ed'), ObjectId('6574895ea0c4a46f9bfb75ee'), ObjectId('6574895ea0c4a46f9bfb75ef'), ObjectId('6574895ea0c4a46f9bfb75f0'), ObjectId('6574895ea0c4a46f9bfb75f1'), ObjectId('6574895ea0c4a46f9bfb75f2'), ObjectId('6574895ea0c4a46f9bfb75f3'), ObjectId('6574895ea0c4a46f9bfb75f4'), ObjectId('6574895ea0c4a46f9bfb75f5'), ObjectId('6574895ea0c4a46f9bfb75f6'), ObjectId('6574895ea0c4a46f9bfb75f7'), ObjectId('6574895ea0c4a46f9bfb75f8'), ObjectId('6574895ea0c4a46f9bfb75f9'), ObjectId('6574895ea0c4a46f9bfb75fa'), ObjectId('6574895ea0c4a46f9bfb75fb'), ObjectId('6574895ea0c4a46f9bfb75fc'), ObjectId('6574895ea0c4a46f9bfb75fd'), ObjectId('6574895ea0c4a46f9bfb75

## Question 1  

In [11]:
cur = kick.aggregate([
    {"$group": {"_id": "$ID", "name": {"$first": "$name"}, "pledged_number": {"$first": "$usd pledged"}}},
    {"$sort": {"pledged_number": -1}},
    {"$limit": 5}
])

result = list(cur)
result

[{'_id': 85964225,
  'name': 'Debut Album from Michael Adam ',
  'pledged_number': 'US'},
 {'_id': 1701277493,
  'name': 'THE SHELLS ï¿½ AUSFLUG NACH NEU-FRIEDENWALD',
  'pledged_number': '9999.268739'},
 {'_id': 218218259,
  'name': 'True North ï¿½ Repurposed Sailcloth Products',
  'pledged_number': '9996.0'},
 {'_id': 1538904209,
  'name': 'Holo ï¿½ Smartphone & Tablet Hologram',
  'pledged_number': '9994.32696132'},
 {'_id': 1247285954,
  'name': '2016 Gaming Calendar',
  'pledged_number': '9994.0'}]

## Question 2

In [16]:
cur = kick.aggregate([
    {"$match": {"state": "successful"}},
    {"$count": "successful_count"}
])

result = list(cur)
print(result)


[{'successful_count': 53040}]


## Question 3

In [18]:
cur = kick.aggregate([
    {"$group": {"_id": "$category", "count": {"$sum": 1}}}
])

result = list(cur)
print(result)


[{'_id': 'Photography', 'count': 2239}, {'_id': 'Kids', 'count': 109}, {'_id': 'Technology', 'count': 2690}, {'_id': '3D Printing', 'count': 271}, {'_id': 'Latin', 'count': 63}, {'_id': 'Comedy', 'count': 923}, {'_id': 'Performance Art', 'count': 855}, {'_id': 'Art', 'count': 3358}, {'_id': 'Music Videos', 'count': 299}, {'_id': 'Architecture', 'count': 300}, {'_id': 'Animation', 'count': 1017}, {'_id': 'Crafts', 'count': 1834}, {'_id': 'Nature', 'count': 219}, {'_id': 'Print', 'count': 288}, {'_id': 'Plays', 'count': 539}, {'_id': 'Web', 'count': 2017}, {'_id': 'Science Fiction', 'count': 274}, {'_id': 'Literary Spaces', 'count': 10}, {'_id': 'Sculpture', 'count': 737}, {'_id': 'Jewelry', 'count': 472}, {'_id': 'Vegan', 'count': 229}, {'_id': "Children's Books", 'count': 2686}, {'_id': 'Translations', 'count': 76}, {'_id': 'Nonfiction', 'count': 3390}, {'_id': 'Woodworking', 'count': 433}, {'_id': 'Family', 'count': 130}, {'_id': 'Glass', 'count': 51}, {'_id': 'Food', 'count': 4612}, 

In [23]:
#result = kick.delete_many({})
#result

DeleteResult({'n': 0, 'ok': 1.0}, acknowledged=True)

## Question 4

In [31]:
cur = kick.aggregate([
    {"$match": {"country": "FR", "launched_year": {"$lte": 2016}}},
    {"$count": "french_project_launched_before_2016"}
])

result = list(cur)
print(result)

[{'french_project_launched_before_2016': 777}]


## Question 5

In [32]:
cur = kick.aggregate([
    {"$match": {"country": "US", "pledged": {"$gte": 200000}}},
    {"$count": "US project which plegeded more than 200 000 USD"}
])

result = list(cur)
print(result)

[{'US project which plegeded more than 200 000 USD': 374}]


## Question 6 

In [33]:
cur = kick.aggregate([
    {"$match": {"name": {"$regex": "Sport", "$options": "i"}}}, 
    {"$count": "sport_projects_count"}
])

result = list(cur)
print(result)

[{'sport_projects_count': 502}]
